# EOP Visualization

In [1]:
import numpy as np
import geopandas as gpd
import plotly.graph_objects as go

## 1 - Loading GeoJSON file and visualizing a 'spherical Earth'

In [2]:
# Load country GeoJSON file
gdf = gpd.read_file("countries.geo.json")
gdf

id                  name  \
0    AFG           Afghanistan   
1    AGO                Angola   
2    ALB               Albania   
3    ARE  United Arab Emirates   
4    ARG             Argentina   
..   ...                   ...   
175  PSE             West Bank   
176  YEM                 Yemen   
177  ZAF          South Africa   
178  ZMB                Zambia   
179  ZWE              Zimbabwe   

                                              geometry  
0    POLYGON ((61.21082 35.65007, 62.23065 35.27066...  
1    MULTIPOLYGON (((16.32653 -5.87747, 16.57318 -6...  
2    POLYGON ((20.59025 41.8554, 20.46318 41.51509,...  
3    POLYGON ((51.57952 24.2455, 51.75744 24.29407,...  
4    MULTIPOLYGON (((-65.5 -55.2, -66.45 -55.25, -6...  
..                                                 ...  
175  POLYGON ((35.54566 32.39399, 35.54525 31.7825,...  
176  POLYGON ((53.10857 16.65105, 52.38521 16.38241...  
177  POLYGON ((31.521 -29.25739, 31.32556 -29.40198...  
178  POLYGON ((32.75938 -9.2306, 33.23139 -9.67672,...  
179  POLYGON ((31.19141 -22.25151, 30.65986 -22.151...  

[180 rows x 3 columns]

In [3]:
# Convert geodetic (lon, lat) to 3D Cartesian coordinates on a slightly inflated sphere
def geo_to_cartesian(lon, lat, radius=1.001):
    lon = np.radians(lon)
    lat = np.radians(lat)
    x = radius * np.cos(lat) * np.cos(lon)
    y = radius * np.cos(lat) * np.sin(lon)
    z = radius * np.sin(lat)
    return x, y, z

# Empty list to store traces defined in GeoJSON file
trace_list = []

for _, row in gdf.iterrows():
    # Extract geometry (Polygon or MultiPolygon) for each feature
    geom = row['geometry']

    # always work with a list of polygons. If MultiPolygon, use the geoms method to make it into a list of polygons,
    if geom.geom_type == 'Polygon':
        polygons = [geom]
    elif geom.geom_type == 'MultiPolygon':
        polygons = list(geom.geoms)
    else:
        # skip anything that's not polygonal
        continue 


    for poly in polygons:
        # Extract the exterior boundary coordinates from the Polygon
        coords = np.array(poly.exterior.coords)
        lon, lat = coords[:, 0], coords[:, 1]

        # Convert geodetic coordinates to 3D Cartesian using a fixed-radius sphere
        # (Earth is actually oblate, but this approximation is sufficient for visualization)
        x, y, z = geo_to_cartesian(lon, lat)

        # Append the 3D curve as a Plotly Scatter3d line trace
        trace_list.append(go.Scatter3d(x=x, y=y, z=z,
                                       mode='lines',
                                       line=dict(color='magenta', width=2),
                                       showlegend=False ))

# Adding a sphere for visual context of Earth
phi = np.linspace(0, 2 * np.pi, 100)            # 1D Numpy Array of longitude angle, phi, 0-360 degrees, linearly spaced
theta = np.linspace(0, np.pi, 100)              # 1D Numpy Array Latitude angle, theta, 0-180 degrees, linearly spaced

# Generate 2D grids of x, y, z coordinates on the sphere surface
# np.outer is used to compute all pairwise combinations of spherical components without explicit meshgrid
x = np.outer(np.cos(phi), np.sin(theta))        # x[i,j] = cos(phi[i]) * sin(theta[j])
y = np.outer(np.sin(phi), np.sin(theta))        # y[i,j] = sin(phi[i]) * sin(theta[j])
z = np.outer(np.ones_like(phi), np.cos(theta))  # z[i,j] = cos(theta[j]), broadcasted across phi

# Surface of our spherical Earth
surface = go.Surface(x=x, y=y, z=z,
                     opacity=0.95,
                     showscale=False,
                     surfacecolor=z,         # surfacecolor controls which scalar field (e.g. z) drives the colorscale mapping on the surface
                     colorscale=[            # Define a custom colorscale to simulate ocean blue shading
                         [0, '#003366'],     # - [0, color] applies to the minimum value of z (south pole, z ≈ -1)
                         [1, '#3399FF']      # - [1, color] applies to the maximum value of z (north pole, z ≈ +1)
                                ])           # Plotly automatically maps z-values to this 0–1 range and interpolates colors in between

# Invoke the .Figure method in plotly and add the data for plot
fig = go.Figure(data=[surface] + trace_list)
fig.update_layout(scene=dict(xaxis=dict(visible=False),
                             yaxis=dict(visible=False),
                             zaxis=dict(visible=False),
                             aspectmode='data',
                             bgcolor='black'),
                  margin=dict(t=0, r=0, l=0, b=0),
                  width=800,
                  height=800)
fig.show()

## 2 - ECI vs ECEF frame

In [4]:
import sys
import os

# Dynamically get the absolute path to the repo root
current_file = os.path.abspath("")
#print(current_file)
project_folder_path = os.path.abspath(os.path.join(current_file, "..", ".."))
#print(project_folder_path)

# Add the project folder to Python’s module search path to enable importing custom project modules
if project_folder_path not in sys.path:
    sys.path.insert(0, project_folder_path)

from AttitudeKinematicsLib.EulerAngles import *